# Online clustering of stream data

<b>Project : MLPro - The integrative middleware framework for standardized machine learning</b> <br>
<b>Package : [mlpro_int_river](https://mlpro-int-river.readthedocs.io/en/latest/)</b> <br>
<b>Module : [howto_oa_ca_003_run_kmeans_2d_static_normalized.py](https://github.com/fhswf/MLPro-Int-River/blob/main/test/howtos/oa/howto_oa_ca_003_run_kmeans_2d_static_normalized.py)</b><br>
<b>Version : 1.3.1</b>

## Introduction

This module demonstrates online cluster analysis of normalized static 2D random point clouds using the wrapped River implementation of stream algorithm KMeans. To this regard, the systematics of sub-framework MLPro-OA-Streams for online adaptive stream processing is used to implement a scenario consisting of a custom workflow and a native benchmark stream.

In particular you will learn:

1. How to set up, run and visualize an online adaptive custom stream processing scenario 

2. How to reuse wrapped River algorithms in own custom stream processing workflows

3. How to reuse native MLPro benchmark streams

4. How to reuse native MLPro online adaptive min-max normalization for data preprocessing

## Preparation

### 1. Install Python
First, ensure you have Python installed on your system. Jupyter Notebooks run on Python, so this is a prerequisite.
- Windows: Download and install Python from python.org.
- macOS: Python 2.7 is pre-installed, but it's recommended to install the latest version of Python 3.
- Linux: Python usually comes pre-installed, but you can use your package manager to install the latest version.

### 2. Install Jupyter Notebook
You can install Jupyter Notebook using Python's package manager, pip. Open your command prompt or terminal and run the following command: <br>
&emsp;<code>pip install notebook</code>

### 3. Launch Jupyter Notebook
Once Jupyter Notebook is installed, you can launch it by running: <br>
&emsp;<code>jupyter notebook</code><br>
This command will start a local server and open the Jupyter Notebook interface in your default web browser.

### 4. Install MLPro-Int-River
You need to install the MLPro-Int-River wrapper package, which integrates MLPro with River, to your virtual environment by running: <br>
&emsp;<code>pip install mlpro-int-river[full]</code>

## Executable Code

### 1. Import the related modules

In [1]:
from mlpro.bf.streams.streams import *
from mlpro.bf.various import Log
from mlpro.oa.streams import *
from mlpro_int_river.wrappers.clusteranalyzers import WrRiverKMeans2MLPro

### 2. Prepare a scenario for Static 2D Point Clouds

In [2]:
class Static2DScenario(OAScenario):

    C_NAME = 'Static2DScenario'

    def _setup(self, p_mode, p_ada: bool, p_visualize: bool, p_logging):

        # 2.1 Get stream from StreamMLProClouds
        stream = StreamMLProClouds( p_num_dim = 2,
                                    p_num_instances = 2000,
                                    p_num_clouds = 5,
                                    p_seed = 1,
                                    p_radii=[100],
                                    p_logging=Log.C_LOG_NOTHING )

        # 2.2 Set up a stream workflow based on a custom stream task

        # 2.2.1 Creation of a workflow
        workflow = OAWorkflow(p_name='Cluster Analysis using KMeans@River',
                              p_range_max=OAWorkflow.C_RANGE_NONE,
                              p_ada=p_ada,
                              p_visualize=p_visualize,
                              p_logging=p_logging)


        # 2.2.2 Creation of tasks and add them to the workflow

        # Boundary detector 
        task_bd = BoundaryDetector(p_name='#1: Boundary Detector', 
                                   p_ada=True, 
                                   p_visualize=p_visualize,   
                                   p_logging=p_logging)
        
        workflow.add_task(p_task = task_bd)

        # MinMax-Normalizer
        task_norm_minmax = NormalizerMinMax(p_name='#2: Normalizer MinMax', 
                                            p_ada=True,
                                            p_visualize=p_visualize, 
                                            p_logging=p_logging )

        task_bd.register_event_handler(
            p_event_id=BoundaryDetector.C_EVENT_ADAPTED,
            p_event_handler=task_norm_minmax.adapt_on_event
            )
        
        workflow.add_task(p_task = task_norm_minmax, p_pred_tasks=[task_bd])

        # Cluster Analyzer
        task_clusterer = WrRiverKMeans2MLPro( p_name='#3: KMeans@River',
                                             p_n_clusters=5,
                                             p_halflife=0.05, 
                                             p_sigma=-1.0, 
                                             p_seed=62,
                                             p_visualize=p_visualize,
                                             p_logging=p_logging )
        
        task_norm_minmax.register_event_handler( p_event_id=NormalizerMinMax.C_EVENT_ADAPTED,
                                                 p_event_handler=task_clusterer.renormalize_on_event )
        
        workflow.add_task(p_task = task_clusterer, p_pred_tasks=[task_norm_minmax])

        # 2.3 Return stream and workflow
        return stream, workflow

### 3. Prepare demo/unit test mode

In [3]:
if __name__ == '__main__':
    cycle_limit = 1000
    logging     = Log.C_LOG_ALL
    visualize   = True
    step_rate   = 2
else:
    cycle_limit = 2
    logging     = Log.C_LOG_NOTHING
    visualize   = False
    step_rate   = 1

### 4. Instantiate the stream scenario

In [4]:
myscenario = Static2DScenario(
    p_mode=Mode.C_MODE_REAL,
    p_cycle_limit=cycle_limit,
    p_visualize=visualize,
    p_logging=logging)

2024-06-05  15:07:34.190702  I  OA-Scenario "Static2DScenario": Instantiated 
2024-06-05  15:07:34.190702  I  OA-Workflow "Cluster Analysis using KMeans@River": Instantiated 
2024-06-05  15:07:34.190702  I  OA-Task "#1: Boundary Detector": Instantiated 
2024-06-05  15:07:34.191898  S  OA-Task "#1: Boundary Detector": Adaptivity switched on 
2024-06-05  15:07:34.191898  I  OA-Workflow "Cluster Analysis using KMeans@River": Adding task "#1: Boundary Detector" 
2024-06-05  15:07:34.191898  I  OA-Task "#2: Normalizer MinMax": Instantiated 
2024-06-05  15:07:34.191898  S  OA-Task "#2: Normalizer MinMax": Adaptivity switched on 
2024-06-05  15:07:34.191898  I  OA-Workflow "Cluster Analysis using KMeans@River": Adding task "#2: Normalizer MinMax" 
2024-06-05  15:07:34.191898  I  River Cluster Analyzer KMeans "#3: KMeans@River": Instantiated 
2024-06-05  15:07:34.191898  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptivity switched on 
2024-06-05  15:07:34.191898  I  River Cluster A

### 5. Reset and run own stream scenario

#### 5.1. Reset stream scenario

In [5]:
myscenario.reset()

2024-06-05  15:07:34.205351  I  OA-Scenario "Static2DScenario": Process time 0:00:00 : Scenario reset with seed 1 


#### 5.2. Run stream scenario

In [6]:
if __name__ == '__main__':
    myscenario.init_plot( p_plot_settings=PlotSettings( p_view = PlotSettings.C_VIEW_ND,
                                                        p_step_rate = step_rate ) )
    input('\nPlease arrange all windows and press ENTER to start stream processing...')

tp_before           = datetime.now()
myscenario.run()
tp_after            = datetime.now()
tp_delta            = tp_after - tp_before
duraction_sec       = ( tp_delta.seconds * 1000000 + tp_delta.microseconds + 1 ) / 1000000
myscenario.log(Log.C_LOG_TYPE_S, 'Duration [sec]:', round(duraction_sec,2), ', Cycles/sec:', round(cycle_limit/duraction_sec,2))

2024-06-05  15:07:34.223576  S  OA-Workflow "Cluster Analysis using KMeans@River": Init plot 
2024-06-05  15:07:34.437528  S  OA-Task "#1: Boundary Detector": Init plot 
2024-06-05  15:07:34.627534  S  OA-Task "#2: Normalizer MinMax": Init plot 
2024-06-05  15:07:34.828608  S  River Cluster Analyzer KMeans "#3: KMeans@River": Init plot 

Please arrange all windows and press ENTER to start stream processing...
2024-06-05  15:07:39.431559  S  OA-Scenario "Static2DScenario": Process time 0:00:05.226208 : Start of processing 
2024-06-05  15:07:39.464702  S  OA-Scenario "Static2DScenario": Process time 0:00:05.259351 : Start of cycle 0 
2024-06-05  15:07:39.464702  S  OA-Workflow "Cluster Analysis using KMeans@River": Started synchronously 
2024-06-05  15:07:39.523610  S  OA-Workflow "Cluster Analysis using KMeans@River": Init plot 
2024-06-05  15:07:39.571890  S  OA-Workflow "Cluster Analysis using KMeans@River": Update plot 
2024-06-05  15:07:39.573895  S  OA-Task "#1: Boundary Detector":

F:\sciebo\800_CollaborationWorks\802_CommonCodeBase\develop\MLPro\MLPro\src\mlpro\bf\streams\basics.py:1205: UserWarning: Attempting to set identical low and high xlims makes transformation singular; automatically expanding.
  p_settings.axes.set_xlim( self._plot_2d_xmin, self._plot_2d_xmax )
F:\sciebo\800_CollaborationWorks\802_CommonCodeBase\develop\MLPro\MLPro\src\mlpro\bf\streams\basics.py:1206: UserWarning: Attempting to set identical low and high ylims makes transformation singular; automatically expanding.
  p_settings.axes.set_ylim( self._plot_2d_ymin, self._plot_2d_ymax )
F:\sciebo\800_CollaborationWorks\802_CommonCodeBase\develop\MLPro\MLPro\src\mlpro\bf\math\normalizers\basics.py:129: RuntimeWarning: divide by zero encountered in divide
  p_data = np.multiply(p_data, 1 / self._param[0]) + \
F:\sciebo\800_CollaborationWorks\802_CommonCodeBase\develop\MLPro\MLPro\src\mlpro\bf\math\normalizers\basics.py:130: RuntimeWarning: invalid value encountered in divide
  (self._param[1] 

2024-06-05  15:07:39.658852  S  OA-Task "#1: Boundary Detector": Started synchronously 
2024-06-05  15:07:39.658852  I  OA-Task "#1: Boundary Detector": Checked in to shared object 
2024-06-05  15:07:39.658852  S  OA-Task "#1: Boundary Detector": Adaptation started 
2024-06-05  15:07:39.658852  S  OA-Task "#1: Boundary Detector": Adaptation on new instance 1 
2024-06-05  15:07:39.658852  S  OA-Task "#1: Boundary Detector": Policy adapted 
2024-06-05  15:07:39.658852  S  OA-Task "#1: Boundary Detector": Event "ADAPTED" fired 
2024-06-05  15:07:39.658852  I  OA-Task "#1: Boundary Detector": Calling handler 0 
2024-06-05  15:07:39.658852  S  OA-Task "#2: Normalizer MinMax": Event "ADAPTED" fired 
2024-06-05  15:07:39.658852  I  OA-Task "#2: Normalizer MinMax": Calling handler 0 
2024-06-05  15:07:39.658852  I  River Cluster Analyzer KMeans "#3: KMeans@River": Renormalization triggered 
2024-06-05  15:07:39.659857  I  River Cluster Analyzer KMeans "#3: KMeans@River": Renormalization comple

2024-06-05  15:07:39.880550  S  OA-Task "#2: Normalizer MinMax": Stopped 
2024-06-05  15:07:39.880550  S  OA-Task "#2: Normalizer MinMax": Event "FINISHED" fired 
2024-06-05  15:07:39.880550  I  OA-Task "#2: Normalizer MinMax": Calling handler 0 
2024-06-05  15:07:39.880550  S  River Cluster Analyzer KMeans "#3: KMeans@River": Started synchronously 
2024-06-05  15:07:39.880550  I  River Cluster Analyzer KMeans "#3: KMeans@River": Checked in to shared object 
2024-06-05  15:07:39.880550  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation started 
2024-06-05  15:07:39.880550  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation on new instance 5 
2024-06-05  15:07:39.880550  I  River Cluster Analyzer KMeans "#3: KMeans@River": Cluster is adapted... 
2024-06-05  15:07:39.880550  S  River Cluster Analyzer KMeans "#3: KMeans@River": Policy adapted 
2024-06-05  15:07:39.880550  S  River Cluster Analyzer KMeans "#3: KMeans@River": Event "ADAPTED" fired 
2024-06-05  15:

2024-06-05  15:07:40.122263  S  OA-Task "#2: Normalizer MinMax": Stopped 
2024-06-05  15:07:40.122263  S  OA-Task "#2: Normalizer MinMax": Event "FINISHED" fired 
2024-06-05  15:07:40.123255  I  OA-Task "#2: Normalizer MinMax": Calling handler 0 
2024-06-05  15:07:40.123255  S  River Cluster Analyzer KMeans "#3: KMeans@River": Started synchronously 
2024-06-05  15:07:40.123255  I  River Cluster Analyzer KMeans "#3: KMeans@River": Checked in to shared object 
2024-06-05  15:07:40.123255  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation started 
2024-06-05  15:07:40.123255  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation on new instance 11 
2024-06-05  15:07:40.123255  I  River Cluster Analyzer KMeans "#3: KMeans@River": Cluster is adapted... 
2024-06-05  15:07:40.123255  S  River Cluster Analyzer KMeans "#3: KMeans@River": Policy adapted 
2024-06-05  15:07:40.123255  S  River Cluster Analyzer KMeans "#3: KMeans@River": Event "ADAPTED" fired 
2024-06-05  15

...

2024-06-05  15:08:20.260936  S  OA-Task "#2: Normalizer MinMax": Stopped 
2024-06-05  15:08:20.260936  S  OA-Task "#2: Normalizer MinMax": Event "FINISHED" fired 
2024-06-05  15:08:20.260936  I  OA-Task "#2: Normalizer MinMax": Calling handler 0 
2024-06-05  15:08:20.261476  S  River Cluster Analyzer KMeans "#3: KMeans@River": Started synchronously 
2024-06-05  15:08:20.261476  I  River Cluster Analyzer KMeans "#3: KMeans@River": Checked in to shared object 
2024-06-05  15:08:20.261476  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation started 
2024-06-05  15:08:20.261476  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation on new instance 973 
2024-06-05  15:08:20.261476  I  River Cluster Analyzer KMeans "#3: KMeans@River": Cluster is adapted... 
2024-06-05  15:08:20.261476  S  River Cluster Analyzer KMeans "#3: KMeans@River": Policy adapted 
2024-06-05  15:08:20.261476  S  River Cluster Analyzer KMeans "#3: KMeans@River": Event "ADAPTED" fired 
2024-06-05  1

2024-06-05  15:08:20.518808  S  OA-Task "#2: Normalizer MinMax": Stopped 
2024-06-05  15:08:20.518808  S  OA-Task "#2: Normalizer MinMax": Event "FINISHED" fired 
2024-06-05  15:08:20.518808  I  OA-Task "#2: Normalizer MinMax": Calling handler 0 
2024-06-05  15:08:20.518808  S  River Cluster Analyzer KMeans "#3: KMeans@River": Started synchronously 
2024-06-05  15:08:20.518808  I  River Cluster Analyzer KMeans "#3: KMeans@River": Checked in to shared object 
2024-06-05  15:08:20.518808  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation started 
2024-06-05  15:08:20.518808  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation on new instance 979 
2024-06-05  15:08:20.518808  I  River Cluster Analyzer KMeans "#3: KMeans@River": Cluster is adapted... 
2024-06-05  15:08:20.518808  S  River Cluster Analyzer KMeans "#3: KMeans@River": Policy adapted 
2024-06-05  15:08:20.518808  S  River Cluster Analyzer KMeans "#3: KMeans@River": Event "ADAPTED" fired 
2024-06-05  1

2024-06-05  15:08:20.756878  S  OA-Task "#2: Normalizer MinMax": Stopped 
2024-06-05  15:08:20.756878  S  OA-Task "#2: Normalizer MinMax": Event "FINISHED" fired 
2024-06-05  15:08:20.756878  I  OA-Task "#2: Normalizer MinMax": Calling handler 0 
2024-06-05  15:08:20.756878  S  River Cluster Analyzer KMeans "#3: KMeans@River": Started synchronously 
2024-06-05  15:08:20.756878  I  River Cluster Analyzer KMeans "#3: KMeans@River": Checked in to shared object 
2024-06-05  15:08:20.756878  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation started 
2024-06-05  15:08:20.756878  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation on new instance 985 
2024-06-05  15:08:20.756878  I  River Cluster Analyzer KMeans "#3: KMeans@River": Cluster is adapted... 
2024-06-05  15:08:20.756878  S  River Cluster Analyzer KMeans "#3: KMeans@River": Policy adapted 
2024-06-05  15:08:20.756878  S  River Cluster Analyzer KMeans "#3: KMeans@River": Event "ADAPTED" fired 
2024-06-05  1

2024-06-05  15:08:20.983724  S  OA-Task "#2: Normalizer MinMax": Stopped 
2024-06-05  15:08:20.983724  S  OA-Task "#2: Normalizer MinMax": Event "FINISHED" fired 
2024-06-05  15:08:20.983724  I  OA-Task "#2: Normalizer MinMax": Calling handler 0 
2024-06-05  15:08:20.983724  S  River Cluster Analyzer KMeans "#3: KMeans@River": Started synchronously 
2024-06-05  15:08:20.983724  I  River Cluster Analyzer KMeans "#3: KMeans@River": Checked in to shared object 
2024-06-05  15:08:20.983724  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation started 
2024-06-05  15:08:20.983724  S  River Cluster Analyzer KMeans "#3: KMeans@River": Adaptation on new instance 991 
2024-06-05  15:08:20.983724  I  River Cluster Analyzer KMeans "#3: KMeans@River": Cluster is adapted... 
2024-06-05  15:08:20.983724  S  River Cluster Analyzer KMeans "#3: KMeans@River": Policy adapted 
2024-06-05  15:08:20.983724  S  River Cluster Analyzer KMeans "#3: KMeans@River": Event "ADAPTED" fired 
2024-06-05  1

2024-06-05  15:08:21.192888  S  OA-Task "#1: Boundary Detector": Started synchronously 
2024-06-05  15:08:21.192888  I  OA-Task "#1: Boundary Detector": Checked in to shared object 
2024-06-05  15:08:21.192888  S  OA-Task "#1: Boundary Detector": Adaptation started 
2024-06-05  15:08:21.192888  S  OA-Task "#1: Boundary Detector": Adaptation on new instance 997 
2024-06-05  15:08:21.192888  S  OA-Task "#1: Boundary Detector": Policy not adapted 
2024-06-05  15:08:21.192888  S  OA-Task "#1: Boundary Detector": Adaptation done without changes 
2024-06-05  15:08:21.192888  I  OA-Task "#1: Boundary Detector": Checked out from shared object 
2024-06-05  15:08:21.192888  S  OA-Task "#1: Boundary Detector": Update plot 
2024-06-05  15:08:21.214890  S  OA-Task "#1: Boundary Detector": Stopped 
2024-06-05  15:08:21.214890  S  OA-Task "#1: Boundary Detector": Event "FINISHED" fired 
2024-06-05  15:08:21.214890  I  OA-Task "#1: Boundary Detector": Calling handler 0 
2024-06-05  15:08:21.214890  S 

##### 5.3. Recap the run

In [7]:
clusters            = myscenario.get_workflow()._tasks[2].get_clusters()
number_of_clusters  = len(clusters)

myscenario.log(Log.C_LOG_TYPE_I, '-------------------------------------------------------')
myscenario.log(Log.C_LOG_TYPE_I, '-------------------------------------------------------')
myscenario.log(Log.C_LOG_TYPE_I, 'Here is the recap of the cluster analyzer')
myscenario.log(Log.C_LOG_TYPE_I, 'Number of clusters: ', number_of_clusters)
for x in range(number_of_clusters):
    myscenario.log(Log.C_LOG_TYPE_I, 'Center of Cluster ', str(x+1), ': ', list(clusters[x].centroid.value))
    myscenario.log(Log.C_LOG_TYPE_I, 'Size of Cluster ', str(x+1), ': ', clusters[x].size.value)
myscenario.log(Log.C_LOG_TYPE_I, '-------------------------------------------------------')
myscenario.log(Log.C_LOG_TYPE_I, '-------------------------------------------------------')

if __name__ == '__main__':
    input('Press ENTER to exit...')

2024-06-05  15:08:21.386886  I  OA-Scenario "Static2DScenario": ------------------------------------------------------- 
2024-06-05  15:08:21.387888  I  OA-Scenario "Static2DScenario": ------------------------------------------------------- 
2024-06-05  15:08:21.387888  I  OA-Scenario "Static2DScenario": Here is the recap of the cluster analyzer 
2024-06-05  15:08:21.387888  I  OA-Scenario "Static2DScenario": Number of clusters:  5 
2024-06-05  15:08:21.387888  I  OA-Scenario "Static2DScenario": Center of Cluster  1 :  [-0.031083705611887356, 0.6725674752840154] 
2024-06-05  15:08:21.387888  I  OA-Scenario "Static2DScenario": Size of Cluster  1 :  646 
2024-06-05  15:08:21.387888  I  OA-Scenario "Static2DScenario": Center of Cluster  2 :  [-0.1982983973034259, -0.8137708361752488] 
2024-06-05  15:08:21.387888  I  OA-Scenario "Static2DScenario": Size of Cluster  2 :  354 
2024-06-05  15:08:21.387888  I  OA-Scenario "Static2DScenario": Center of Cluster  3 :  [0.04632631029878387, -2.087